# To visualize your training result
we use `hiplot` to visualize your training result in a jupyter notebook 

In [1]:
!pip install hiplot

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple


In [2]:
import os
import sys
import time
import numpy as np
import pickle as pkl
import hiplot as hip

In [3]:
from litebo.optimizer.generic_smbo import SMBO
from test.reproduction.so.so_benchmark_function import get_problem
from test.reproduction.test_utils import timeit, seeds

/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/pyparsing.py:3190: FutureWarning: Possible set intersection at position 3
  self.re = re.compile(self.reString)


In [4]:
problem_str = 'branin'
max_runs = 100
initial_runs = 3
init_strategy = 'random_explore_first'
surrogate_type = 'gp'
optimizer_str = 'scipy'
if optimizer_str == 'scipy':
    acq_optimizer_type = 'random_scipy'
elif optimizer_str == 'local':
    acq_optimizer_type = 'local_random'
else:
    raise ValueError('Unknown optimizer %s' % args.optimizer)
rep = 1
start_id = 0
mth = 'litebo'

problem = get_problem(problem_str)
cs = problem.get_configspace(optimizer='smac')
time_limit_per_trial = 600
task_id = '%s_%s' % (mth, problem_str)

# Train and get the config_list and perf_list

In [5]:
def evaluate(mth, run_i, seed):
    print(mth, run_i, seed, '===== start =====', flush=True)

    def objective_function(config):
        y = problem.evaluate_config(config)
        res = dict()
        res['config'] = config
        res['objs'] = (y,)
        res['constraints'] = None
        return res

    bo = SMBO(objective_function, cs,
              surrogate_type=surrogate_type,            # default: gp
              acq_optimizer_type=acq_optimizer_type,    # default: random_scipy
              initial_runs=initial_runs,                # default: 3
              init_strategy=init_strategy,              # default: random_explore_first
              max_runs=max_runs,
              time_limit_per_trial=time_limit_per_trial, task_id=task_id, random_state=seed)
    # bo.run()
    config_list = []
    perf_list = []
    time_list = []
    global_start_time = time.time()
    for i in range(max_runs):
        config, trial_state, objs, trial_info = bo.iterate()
        global_time = time.time() - global_start_time
        print(seed, i, objs, config, trial_state, trial_info, 'time=', global_time)
        config_list.append(config)
        perf_list.append(objs[0])
        time_list.append(global_time)

    return config_list, perf_list, time_list


with timeit('%s all' % (mth,)):
    for run_i in range(start_id, start_id + rep):
        seed = seeds[run_i]
        with timeit('%s %d %d' % (mth, run_i, seed)):
            # Evaluate
            config_list, perf_list, time_list = evaluate(mth, run_i, seed)

            # Save result
            print('=' * 20)
            print(seed, mth, config_list, perf_list, time_list)
            print(seed, mth, 'best perf', np.min(perf_list))

            timestamp = time.strftime('%Y-%m-%d-%H-%M-%S', time.localtime(time.time()))
            dir_path = 'logs/so_benchmark_%s_%d/%s/' % (problem_str, max_runs, mth)
            file = 'benchmark_%s_%04d_%s.pkl' % (mth, seed, timestamp)
            if not os.path.exists(dir_path):
                os.makedirs(dir_path)
            with open(os.path.join(dir_path, file), 'wb') as f:
                save_item = (config_list, perf_list, time_list)
                pkl.dump(save_item, f)
            print(dir_path, file, 'saved!', flush=True)

[litebo all]Start.
[litebo 0 4774]Start.
litebo 0 4774 ===== start =====
[INFO] [2021-03-16 15:08:25,714:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 1-th iteration, the objective value: (24.129964413622268,)
4774 0 (24.129964413622268,) Configuration:
  x1, Value: 2.5
  x2, Value: 7.5
 0 None time= 0.02422618865966797
[INFO] [2021-03-16 15:08:25,738:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 2-th iteration, the objective value: (266.87545772568916,)
4774 1 (266.87545772568916,) Configuration:
  x1, Value: -4.650963559365345
  x2, Value: 0.15097536559954217
 0 None time= 0.04910898208618164
[INFO] [2021-03-16 15:08:25,765:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 3-th iteration, the objective value: (112.99109683630043,)
4774 2 (112.99109683630043,) Configuration:
  x1, Value: 9.868015819326814
  x2, Value: 13.441442125698543
 0 None time= 0.07566308975219727
[INFO] [2021-03-16 15:08:26,121:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 4-th iteration, th

/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "


[INFO] [2021-03-16 15:08:42,035:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 28-th iteration, the objective value: (0.4575028033643669,)
4774 27 (0.4575028033643669,) Configuration:
  x1, Value: 9.53115138424054
  x2, Value: 2.4931062506825405
 0 None time= 16.34485101699829


/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "


[INFO] [2021-03-16 15:08:43,188:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 29-th iteration, the objective value: (0.4589256842667542,)
4774 28 (0.4589256842667542,) Configuration:
  x1, Value: 3.0306354156527853
  x2, Value: 2.4077387186865984
 0 None time= 17.497545957565308


...

/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/le

/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/le

/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/learning/gaussian_process/gpr.py:338: UserWarning: Predicted variances smaller than 0. Setting those variances to 0.
  warnings.warn("Predicted variances smaller than 0. "
/opt/anaconda3/envs/lite_bo/lib/python3.7/site-packages/skopt/le

[INFO] [2021-03-16 15:10:18,959:Lite-BO-litebo_branin-[2021-03-16 15:08:25]] In the 100-th iteration, the objective value: (0.39788806543439925,)
4774 99 (0.39788806543439925,) Configuration:
  x1, Value: 3.1419756492162865
  x2, Value: 2.274642526374721
 0 None time= 113.26844501495361
4774 litebo [Configuration:
  x1, Value: 2.5
  x2, Value: 7.5
, Configuration:
  x1, Value: -4.650963559365345
  x2, Value: 0.15097536559954217
, Configuration:
  x1, Value: 9.868015819326814
  x2, Value: 13.441442125698543
, Configuration:
  x1, Value: 4.53859534106417
  x2, Value: 7.72710041549182
, Configuration:
  x1, Value: -2.947029424995461
  x2, Value: 6.895503063437221
, Configuration:
  x1, Value: 7.340297638028138
  x2, Value: 6.708246755199158
, Configuration:
  x1, Value: 1.1332191046870355
  x2, Value: 6.774056145990567
, Configuration:
  x1, Value: -5.0
  x2, Value: 8.404559308713631
, Configuration:
  x1, Value: 0.8299486522082056
  x2, Value: 7.1509792109637536
, Configuration:
  x1, Va

[litebo 0 4774]Total time = 0 hours, 1 minutes, 53 seconds.
[litebo all]Total time = 0 hours, 1 minutes, 53 seconds.


In [6]:
config_list

[Configuration:
   x1, Value: 2.5
   x2, Value: 7.5,
 Configuration:
   x1, Value: -4.650963559365345
   x2, Value: 0.15097536559954217,
 Configuration:
   x1, Value: 9.868015819326814
   x2, Value: 13.441442125698543,
 Configuration:
   x1, Value: 4.53859534106417
   x2, Value: 7.72710041549182,
 Configuration:
   x1, Value: -2.947029424995461
   x2, Value: 6.895503063437221,
 Configuration:
   x1, Value: 7.340297638028138
   x2, Value: 6.708246755199158,
 Configuration:
   x1, Value: 1.1332191046870355
   x2, Value: 6.774056145990567,
 Configuration:
   x1, Value: -5.0
   x2, Value: 8.404559308713631,
 Configuration:
   x1, Value: 0.8299486522082056
   x2, Value: 7.1509792109637536,
 Configuration:
   x1, Value: -5.0
   x2, Value: 5.627170264199307,
 Configuration:
   x1, Value: -5.0
   x2, Value: 10.993880383649683,
 Configuration:
   x1, Value: 10.0
   x2, Value: 10.320742564429231,
 Configuration:
   x1, Value: 10.0
   x2, Value: 11.535316871608682,
 Configuration:
   x1, Value: -

In [7]:
config_list[0]

Configuration:
  x1, Value: 2.5
  x2, Value: 7.5

In [8]:
type(config_list[0])

ConfigSpace.configuration_space.Configuration

In [9]:
config_list[0].get_dictionary()

{'x1': 2.5, 'x2': 7.5}

In [10]:
perf_list[0]

24.129964413622268

# prepare the visualize_data

In [11]:
visualize_data = []
for config in config_list:
    visualize_data.append(config.get_dictionary())
for tmp1, tmp2 in zip(visualize_data, perf_list):
    tmp1['perf'] = tmp2

In [12]:
visualize_data

[{'x1': 2.5, 'x2': 7.5, 'perf': 24.129964413622268},
 {'x1': -4.650963559365345,
  'x2': 0.15097536559954217,
  'perf': 266.87545772568916},
 {'x1': 9.868015819326814,
  'x2': 13.441442125698543,
  'perf': 112.99109683630043},
 {'x1': 4.53859534106417, 'x2': 7.72710041549182, 'perf': 47.896748319314426},
 {'x1': -2.947029424995461,
  'x2': 6.895503063437221,
  'perf': 24.75403074293578},
 {'x1': 7.340297638028138, 'x2': 6.708246755199158, 'perf': 44.20583536156188},
 {'x1': 1.1332191046870355,
  'x2': 6.774056145990567,
  'perf': 19.885317210220816},
 {'x1': -5.0, 'x2': 8.404559308713631, 'perf': 89.86134218826811},
 {'x1': 0.8299486522082056,
  'x2': 7.1509792109637536,
  'perf': 22.15880605746351},
 {'x1': -5.0, 'x2': 5.627170264199307, 'perf': 146.36174028428965},
 {'x1': -5.0, 'x2': 10.993880383649683, 'perf': 51.082944568449676},
 {'x1': 10.0, 'x2': 10.320742564429231, 'perf': 55.49313200785355},
 {'x1': 10.0, 'x2': 11.535316871608682, 'perf': 74.74431237852997},
 {'x1': -2.311047

In [13]:
hip.Experiment.from_iterable(visualize_data).display()

<IPython.core.display.Javascript object>